# Meeting 20221026
- **Excute the bootstrap result without selecting well logs**
- **Try Kirging water level data**
- **Compare corrected water level data with gamma water level data**


Initial setup

In [1]:
import os
import numpy as np
import tTEM_tool as tt
import pandas as pd
import plotly.offline as po
import plotly.graph_objects as go
import plotly.express as px
from pyproj import Transformer
import pykrige as pk
from plotly.offline import init_notebook_mode
init_notebook_mode(connected = True)
#import importlib
#importlib.reload(tt.bootstrap)

In [2]:
os.chdir(r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\well_Utah')
well_info = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\well_Utah\USGSdownload\NWISMapperExport.xlsx'
location = r"C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\Gamma\location.csv"
welllog = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\Plot_with_well_log\Well_log.xlsx'
elevation = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\well_Utah\usgs_water_elevation.csv'
ttemname = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\Plot_with_well_log\PD1_I01_MOD.xyz'
ttemname2 = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\Plot_with_well_log\PD22_I03_MOD.xyz'
DOI = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\Plot_with_well_log\DOID1_DOIStaE.xyz'
time = '2022-3'
def splt_ttem(ttem_df, gwsurface_result):
    def get_distance(group1, group2):
        dis = np.sqrt((group1[0] - group2[0]) ** 2 + (group1[1] - group2[1]) ** 2)
        return dis
    abv_water_table = []
    blw_water_table = []
    ttem_groups = ttem_df.groupby(['UTMX', 'UTMY'])
    well_location = gwsurface_result[['UTMX', 'UTMY']].values
    for name, group in ttem_groups:
        ttem_xy = list(group[['UTMX', 'UTMY']].iloc[0])
        ttem_well_distance = list(map(lambda x: get_distance(ttem_xy, x), well_location))
        match = gwsurface_result.iloc[ttem_well_distance.index(min(ttem_well_distance))]
        elevation = match['water_elevation']
        ttem_abv = group[group['Elevation_End'] >= elevation]
        abv_water_table.append(ttem_abv)
        ttem_blw = group[group['Elevation_End'] < elevation]
        blw_water_table.append(ttem_blw)

    ttem_above = pd.concat(abv_water_table)
    ttem_below = pd.concat(blw_water_table)
    return ttem_above, ttem_below
def plot_bst(dataframe):
    """
    plot bootstrap result

    :param dataframe:
    :return: plotly fig
    """
    fig_hist = go.Figure()
    fig_hist.data = []
    fig_hist.add_trace(go.Histogram(x=dataframe.fine, name='Fine', marker_color='Blue', opacity=0.75))
    fig_hist.add_trace(go.Histogram(x=dataframe.coarse, name='Coarse', marker_color='Red', opacity=0.75))
    if dataframe.mix.sum() == 0:
        print("skip plot mix because there is no data")
    else:
        fig_hist.add_trace(go.Histogram(x=dataframe.mix, name='Mix', marker_color='Green', opacity=0.75))
    fig_hist.update_layout(paper_bgcolor='white',plot_bgcolor='white',font_color='black')
    return fig_hist

In [3]:
water = tt.main.GWSurface(waterwell=well_info)

reading wells in file C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\well_Utah\USGSdownload\NWISMapperExport.xlsx


C:\Users\jldz9\anaconda3\envs\Research\lib\site-packages\openpyxl\worksheet\header_footer.py:48: UserWarning:

Cannot parse header or footer so it will be ignored



375033112561101 Done!
375006112554801 Done!
375112112551202 Done!
375024112542601 Done!
375152112541001 Done!
375152112541001 not able to merge, try to solve the problem by drop duplicates.
375127112530602 Done!
375303112512102 Done!
375338112502801 Done!
375548112500401 Done!
375153112500201 Done!
375153112500201 not able to merge, try to solve the problem by drop duplicates.
375443112495501 Done!
375303112495102 Done!
375233112475701 Done!
375440112500001 Done!
375402112455401 Done!
375523112451902 Done!
375915112442901 Done!
380130112425201 Done!
380033112423101 Done!
All Wells Done!


In [4]:
water_format = water.format(elevation=None, time=time)
water_format13_3 =  water.format(elevation=None, time='2013-3')
water_format12_11 = water.format(elevation=None, time='2012-11')
elevation_diff12_13 = water_format12_11['sl_lev_va2012-11'].subtract(water_format13_3['sl_lev_va2013-3'])
#water_format.dropna(inplace=True)
water_format.to_csv(r'D:\demo.csv')
water_format['water_elevation'] = water_format['sl_lev_va2022-3']

In [5]:
water_diff_krig = pk.ok.OrdinaryKriging(water_format["UTMX"], water_format['UTMY'],elevation_diff12_13)

In [6]:
water_kirg = pk.ok.OrdinaryKriging(water_format["UTMX"], water_format['UTMY'],water_format['sl_lev_va2022-3'])

x = np.arange(np.min(water_format['UTMX'])-5000, np.max(water_format['UTMX'])+5000,1000)
y = np.arange(np.min(water_format['UTMY'])-5000, np.max(water_format['UTMY'])+5000,1000)
z,ss = water_kirg.execute('grid',x, y)
z_diff, ss_diff = water_diff_krig.execute('grid',x,y)
x_grid,y_grid=np.meshgrid(x,y)
x_flat = x_grid.flatten()
y_flat = y_grid.flatten()
z_flat = (z+z_diff).flatten()
water_kirg_org = pd.DataFrame({'UTMX':x_flat,'UTMY':y_flat,'water_elevation':z.flatten()})
water_corrected = pd.DataFrame({'UTMX':x_flat,'UTMY':y_flat,'water_elevation':z_flat})

In [7]:
fig = go.Figure()
trace = go.Scatter3d(x=x_flat,y=y_flat,z=z_flat)
fig.add_trace(trace)
trace_org = tt.plot.generate_trace(water_format,'water')
init_notebook_mode(connected = True)
fig.add_trace(trace_org)
fig.update_layout(scene_aspectmode='data')
                  #scene_aspectratio=dict(x=1,y=1,z=0.3))

In [8]:
from pyproj import Transformer
transformer = Transformer.from_crs('epsg:4326', 'epsg:32612')
location = r'C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\Gamma\location.csv'
location_df = pd.read_csv(location)
long = location_df['X']
lat = location_df['Y']
x, y = transformer.transform(lat, long)
trace_gamma = go.Scatter3d(x=x,y=y,z=location_df['water_level'])
fig.add_trace(trace_gamma)
fig.update_layout(scene_aspectmode='data')

In [9]:
ttem = tt.main.ProcessTTEM(ttem_path=[ttemname, ttemname2],
                                   welllog=welllog,
                                   DOI_path=DOI,
                                   layer_exclude=[])
data = ttem.data()
ttem_match, well_match = tt.bootstrap.select_closest(data,
                                                     tt.process_well.format_well(welllog, upscale=100),distance=500,
                                                       showskip=False)
ttem_above_wt, ttem_below_wt = splt_ttem(data, water_kirg_org)
bootstrap_above = tt.main.ProcessTTEM(ttem_path=ttem_above_wt, welllog=welllog)
bootstrap_above_result = bootstrap_above.ttem_well_connect(distance=500)
bootstrap_below = tt.main.ProcessTTEM(ttem_path=ttem_below_wt, welllog=welllog)
bootstrap_below_result = bootstrap_below.ttem_well_connect(distance=500)

Applying DOI |                                | 77/7968

Exclude layer []
No line was excluded
No point was excluded


Applying DOI |################################| 7968/7968
Formating well logs |################################| 223/223
Selecting closest ttem trace |################################| 223/223


Total of 47 well with in radius (500m), 176 skipped
Reusing cached dataframe...
No layer was excluded
No line was excluded
No point was excluded
Will skip filterting DOI since no DOI file exist


Formating well logs |################################| 223/223
Selecting closest ttem trace |################################| 223/223
connecting ttem with well |########                        | 13/47

...

Bootstraping...
Done!
Reusing cached dataframe...
No layer was excluded
No line was excluded
No point was excluded
Will skip filterting DOI since no DOI file exist


Formating well logs |################################| 223/223
Selecting closest ttem trace |################################| 223/223
connecting ttem with well |#############                   | 20/47

Total of 47 well with in radius (500m), 176 skipped


connecting ttem with well |################################| 47/47
C:\Users\jldz9\OneDrive - University of Missouri\MST\Code\Python\tTEM_test\Plot_with_well_log\tTEM_tool\core\bootstrap.py:185: FutureWarning:

`rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.



Bootstraping...
Done!


In [10]:
ttem_above_match, well_match = tt.bootstrap.select_closest(ttem_above_wt,tt.process_well.format_well(welllog, upscale=100),distance=500,showskip=False)
ttem_below_match,well_match = tt.bootstrap.select_closest(ttem_below_wt,tt.process_well.format_well(welllog, upscale=100),distance=500,showskip=False)

Formating well logs |################################| 223/223
Selecting closest ttem trace |################################| 223/223


Total of 47 well with in radius (500m), 176 skipped


Formating well logs |################################| 223/223
Selecting closest ttem trace |################################| 223/223


Total of 47 well with in radius (500m), 176 skipped


In [11]:
ttem_above_match.shape
ttem_below_match.shape

(278, 16)

In [ ]:
trace_ttem = tt.plot.generate_trace(bootstrap_above.data(),'ttem')
fig.add_trace(trace_ttem)
fig.update_layout(scene_aspectmode='manual',
                  scene_aspectratio=dict(x=1,y=1,z=0.3))

In [13]:
plot_bst(bootstrap_above_result[1])

In [14]:
plot_bst(bootstrap_below_result[1])

In [15]:
ttem_above_wt.Resistivity.plot.hist()

In [16]:
ttem_below_wt.Resistivity.plot.hist()

In [17]:
ttem_above_wt

ID  Line_No  Layer_No      UTMX       UTMY  Elevation_Cell  \
88068  95      130         1  331178.3  4192309.5         1737.76   
88069  95      130         2  331178.3  4192309.5         1736.72   
88070  95      130         3  331178.3  4192309.5         1735.58   
88071  95      130         4  331178.3  4192309.5         1734.34   
88072  95      130         5  331178.3  4192309.5         1733.00   
...    ..      ...       ...       ...        ...             ...   
22397  11      120        11  351164.5  4212750.5         1768.94   
22398  11      120        12  351164.5  4212750.5         1766.51   
22399  11      120        13  351164.5  4212750.5         1763.87   
22400  11      120        14  351164.5  4212750.5         1760.99   
22401  11      120        15  351164.5  4212750.5         1757.87   

       Resistivity  Resistivity_STD  Conductivity  Depth_top  Depth_bottom  \
88068        55.34            2.050       18.0701      0.000         1.000   
88069        43.31            1.652       23.0894      1.000         2.088   
88070        27.91            1.509       35.8295      2.088         3.272   
88071        15.83            1.503       63.1712      3.272         4.560   
88072        10.24            1.418       97.6563      4.560         5.962   
...            ...              ...           ...        ...           ...   
22397        51.28            1.638       19.5008     15.056        17.382   
22398        46.37            1.599       21.5657     17.382        19.913   
22399        40.91            1.566       24.4439     19.913        22.667   
22400        37.46            1.546       26.6951     22.667        25.664   
22401        37.58            1.544       26.6099     25.664        28.925   

       Thickness  Thickness_STD  Elevation_End  
88068      1.000          1.001       1736.760  
88069      1.088          1.001       1735.632  
88070      1.184          1.001       1734.396  
88071      1.288          1.001       1733.052  
88072      1.402          1.001       1731.598  
...          ...            ...            ...  
22397      2.326          1.001       1766.614  
22398      2.531          1.001       1763.979  
22399      2.754          1.001       1761.116  
22400      2.997          1.001       1757.993  
22401      3.261          1.001       1754.609  

[118990 rows x 14 columns]

In [18]:
line100 = data[data['Line_No'] == 100]
line100 = line100[(line100['UTMX'] <= 350539.30) & (line100['UTMX']>349221.50)]

In [19]:
line100['distance'] = np.sqrt(line100['UTMX'].copy()**2 + line100['UTMY'].copy()**2)
line100['distance'] = line100['distance'] - line100['distance'].min()

In [21]:
colorRes = [[0, 'rgb(0,0,190)'],
            [1 / 16, 'rgb(0,75,220)'],
            [2 / 16, 'rgb(0,150,235)'],
            [3 / 16, 'rgb(0,200,255)'],
            [4 / 16, 'rgb(80,240,255)'],
            [5 / 16, 'rgb(30,210,0)'],
            [6 / 16, 'rgb(180,255,30)'],
            [7 / 16, 'rgb(255,255,0)'],
            [8 / 16, 'rgb(255,195,0)'],
            [9 / 16, 'rgb(255,115,0)'],
            [10 / 16, 'rgb(255,0,0)'],
            [11 / 16, 'rgb(255,0,120)'],
            [12 / 16, 'rgb(140,40,180)'],
            [13 / 16, 'rgb(165,70,220)'],
            [14 / 16, 'rgb(195,130,240)'],
            [15 / 16, 'rgb(230,155,240)'],
            [1, 'rgb(230,155,255)']]

#from scipy.interpolate import griddata
#points = np.stack((line100['distance'],line100['Elevation_Cell'])).T
#values = line100['Resistivity']
#grid_z0 = griddata(points,values,(grid_x,grid_y),method='nearest')
#import plotly.express as px
#fig= px.imshow(grid_z0,color_continuous_scale=colorRes)
#fig.show(renderer='browser')
#fig.update_layout(colorscale='colorRes')

In [44]:
grid_y, grid_x = np.mgrid[line100['Elevation_Cell'].max():line100['Elevation_Cell'].min():690j, line100['distance'].min():line100['distance'].max():3120j]
grid_z1 = np.full((690,3120),np.nan)
groups = line100.groupby('distance')
for name, group in groups:
    x_index = np.where((grid_x>=name-1) & (grid_x <=name+1))[1][0]
    for index, line in group.iterrows():
        y_index = np.where((grid_y[:,x_index] <= line['Elevation_Cell']) & (grid_y[:,x_index]>=line['Elevation_End']))[0]
        grid_z1[y_index[0]-2:y_index[-1]+2,x_index-3:x_index+3] = np.log10(line['Resistivity'])

In [52]:
fig=px.imshow(grid_z1,range_color=(0,3),color_continuous_scale=colorRes)
fig.update_layout(paper_bgcolor='white',plot_bgcolor='white',font_color='black')
fig.update_layout(yaxis=dict(title='Elevation (m)',tickmode='array',tickvals=[0,100,200,300,400,500,600]
                             ,ticktext=['1779','1767.5','1756','1744.5','1733','1721.5','1710']),
                  xaxis=dict(title='Distance (m)'))
fig.update_coloraxes(colorbar=dict(ticks='outside',title='Resistivity', tickvals=[0,1,2,3], ticktext=['1','10','100','1000'],tickmode='array',len=0.5))
fig.show(renderer='browser')

In [36]:
fig_surface = go.Figure(data=[go.Surface(z=line100['Elevation_Cell'],x=line100['UTMX'],y=line100['UTMY'])])
fig_surface.show(renderer='browser')